In [58]:
from transformers import CamembertTokenizer, CamembertModel, AutoTokenizer, AutoModel, utils, BertModel, BertTokenizer
import torch
from scipy.spatial.distance import cosine
from bertviz import model_view, head_view
import itertools
from IPython import display
import matplotlib.pyplot as plt
import numpy as np
#utils.logging.set_verbosity_error()  # Suppress standard warnings

First method

In [ ]:
# Initialisation du tokenizer et du modèle CamemBERT
model_version = 'camembert-base'
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = CamembertTokenizer.from_pretrained(model_version)

"""
# Phrases à analyser
#phrase1 = "Il porte son attention sur le problème."
#phrase2 = "Il porte un pot de miel à sa grand-mère."

phrase1 = "Elle éprouve une immense haine pour lui."
phrase2 = "Elle éprouve de grandes difficultés à finir son projet à temps."

#phrase1 = "Il prend un objet dans sa main."
#phrase2 = "Elle prend une décision importante."
"""

#phrase1 = "On court dans le désert."
#phrase2 = "On court le risque de perdre le match."
phrase2 = "Il prend une décision importante."
phrase1 = "Il prend un objet dans sa main."
# Encodage des phrases pour le modèle
inputs = tokenizer(phrase1, phrase2, return_tensors='pt', padding=True)
# Extraction des inputs nécessaires
input_ids = inputs['input_ids']
attention = model(input_ids, attention_mask=inputs['attention_mask']).attentions

# Conversion des IDs de tokens en tokens
tokens = tokenizer.convert_ids_to_tokens(input_ids[0])

# Utilisation de BertViz pour visualiser l'attention

# Tokenisation et création des masques d'attention
tokens_tensor1, attention_mask1 = tokenizer.encode_plus(phrase1, return_tensors='pt').values()
tokens_tensor2, attention_mask2 = tokenizer.encode_plus(phrase2, return_tensors='pt').values()

# Extraction des embeddings
with torch.no_grad():
    outputs1 = model(tokens_tensor1, attention_mask=attention_mask1)
    outputs2 = model(tokens_tensor2, attention_mask=attention_mask2)

# Identification de l'indice du token qu'on souhaite (nécessite parfois ajustement)
index_of_word = 2  # Exemple d'indice, vérifiez le bon index avec tokenizer.tokenize(phrase1)
embedding1 = outputs1.last_hidden_state[0, index_of_word, :]
embedding2 = outputs2.last_hidden_state[0, index_of_word, :]

# Calcul de la similarité cosinus
similarity = 1 - cosine(embedding1, embedding2)

print(f"La similarité cosinus entre les deux utilisations de 'prend' est de {similarity:.2f}")


Second method (better ?)

In [ ]:
# Initialisation du tokenizer et du modèle CamemBERT
model_version = 'camembert-base'
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = CamembertTokenizer.from_pretrained(model_version)

# Phrases à analyser

#phrase1 = "On court dans le désert."
#phrase2 = "On court le risque de perdre le match."

phrase2 = "Il prend une décision importante."
phrase1 = "Il prend un objet dans sa main."

# Tokenisation des phrases en considérant la casse et les subwords
tokens1 = [token.lower() for token in tokenizer.tokenize(phrase1)]
tokens2 = [token.lower() for token in tokenizer.tokenize(phrase2)]

# Mot à chercher, en minuscule pour éviter les problèmes de casse
word = 'prend'.lower()

# Trouver les indices du mot ou de son subword principal dans chaque phrase
index_word1 = next((i for i, token in enumerate(tokens1) if word in token), None)
index_word2 = next((i for i, token in enumerate(tokens2) if word in token), None)

# Encodage et extraction des embeddings si le mot est trouvé dans les deux phrases
if index_word1 is not None and index_word2 is not None:
    inputs1 = tokenizer.encode_plus(phrase1, return_tensors='pt')
    inputs2 = tokenizer.encode_plus(phrase2, return_tensors='pt')

    with torch.no_grad():
        outputs1 = model(**inputs1)
        outputs2 = model(**inputs2)

    embedding1 = outputs1.last_hidden_state[0, index_word1, :]
    embedding2 = outputs2.last_hidden_state[0, index_word2, :]

    # Calcul de la similarité cosinus
    similarity = 1 - cosine(embedding1, embedding2)

    print(f"La similarité cosinus entre les deux utilisations de '{word}' est de {similarity:.2f}")
else:
    print("Impossible de calculer la similarité car le mot n'est pas trouvé dans une ou les deux phrases.")


In [60]:
# Initialisation du tokenizer et du modèle CamemBERT (supposée déjà faite)

model_version = 'camembert-base'
tokenizer = CamembertTokenizer.from_pretrained(model_version)
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
"""
# Phrases avec le verbe 'courir'
phrases = [
    "Il court un péril en allant là-bas.",
    "Le buzz court sur les réseaux sociaux.",
    "Le bruit court dans les couloirs.",
    "Elle court sur la route.",
    "Le danger court dans les zones inexplorées.",
    "Le nuage court dans le ciel orageux.",
    "Le risque court dans chaque décision d'investissement."
]
"""

# Phrases avec le verbe 'faire'
phrases = [
    "Il fait marche arrière concernant ma décision.",
    "Elle fait la lessive tous les samedis pour garder mes vêtements propres.",
    "Julien fait du vélo tous les matins pour rester en forme.",
    "Il fait souvent du cinéma pour attirer la pitié.",
    "On fait une demande officielle pour obtenir l'autorisation nécessaire.",
    "Coralie fait de la boxe pour améliorer ma condition physique et ma concentration."
]

# Verbe à analyser
#word = 'court'

word = 'fait'

# Comparer chaque paire de phrases
for phrase1, phrase2 in itertools.combinations(phrases, 2):
    tokens1 = [token.lower() for token in tokenizer.tokenize(phrase1)]
    tokens2 = [token.lower() for token in tokenizer.tokenize(phrase2)]

    index_word1 = next((i for i, token in enumerate(tokens1) if word in token), None)
    index_word2 = next((i for i, token in enumerate(tokens2) if word in token), None)

    if index_word1 is not None and index_word2 is not None:
        inputs1 = tokenizer.encode_plus(phrase1, return_tensors='pt')
        inputs2 = tokenizer.encode_plus(phrase2, return_tensors='pt')

        with torch.no_grad():
            outputs1 = model(**inputs1)
            outputs2 = model(**inputs2)

        embedding1 = outputs1.last_hidden_state[0, index_word1, :]
        embedding2 = outputs2.last_hidden_state[0, index_word2, :]

        similarity = 1 - cosine(embedding1.numpy(), embedding2.numpy())
        print(f"Similarity for '{word}' between '{phrase1}' and '{phrase2}': {similarity:.2f}")
    else:
        print(f"Impossible de calculer la similarité entre '{phrase1}' et '{phrase2}' car le mot '{word}' n'est pas trouvé dans une des deux phrases.")
        
# Extraction des attentions
attentions1 = outputs1.attentions
attentions2 = outputs2.attentions
# Analyse des attentions pour la première phrase
# Ici, nous prenons les attentions de la dernière couche pour simplifier
first_layer_attentions = attentions1[0]  # Prendre la première couche
attention_scores = first_layer_attentions[0, :, index_word1, :]  # Attention scores du mot "courir"
#print(attention_scores)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Elle fait la lessive tous les samedis pour garder mes vêtements propres.': 0.93
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Julien fait du vélo tous les matins pour rester en forme.': 0.86
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Il fait souvent du cinéma pour attirer la pitié.': 0.94
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'On fait une demande officielle pour obtenir l'autorisation nécessaire.': 0.90
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Coralie fait de la boxe pour améliorer ma condition physique et ma concentration.': 0.74
Similarity for 'fait' between 'Elle fait la lessive tous les samedis pour garder mes vêtements propres.' and 'Julien fait du vélo tous les matins pour rester en forme.': 0.84
Similarity for 'fait' between 'Elle f

In [61]:
# Initialisation du tokenizer et du modèle BERT multilingue
model_version = 'bert-base-multilingual-cased'
tokenizer = BertTokenizer.from_pretrained(model_version)
model = BertModel.from_pretrained(model_version, output_attentions=True)

"""
# Phrases avec le verbe 'courir'
phrases = [
    "Il court un péril en allant là-bas.",
    "Le buzz court sur les réseaux sociaux.",
    "Le bruit court dans les couloirs.",
    "Elle court sur la route.",
    "Le danger court dans les zones inexplorées.",
    "Le nuage court dans le ciel orageux.",
    "Le risque court dans chaque décision d'investissement."
]
"""

# Phrases avec le verbe 'faire'
phrases = [
    "Il fait marche arrière concernant ma décision.",
    "Elle fait la lessive tous les samedis pour garder mes vêtements propres.",
    "Julien fait du vélo tous les matins pour rester en forme.",
    "Il fait souvent du cinéma pour attirer la pitié.",
    "On fait une demande officielle pour obtenir l'autorisation nécessaire.",
    "Coralie fait de la boxe pour améliorer ma condition physique et ma concentration."
]

# Verbe à analyser
#word = 'court'  # À noter que 'court' en français pourrait être traité différemment en multilingue
word= 'fait'
# Comparer chaque paire de phrases
for phrase1, phrase2 in itertools.combinations(phrases, 2):
    tokens1 = [token.lower() for token in tokenizer.tokenize(phrase1)]
    tokens2 = [token.lower() for token in tokenizer.tokenize(phrase2)]

    index_word1 = next((i for i, token in enumerate(tokens1) if word in token), None)
    index_word2 = next((i for i, token in enumerate(tokens2) if word in token), None)

    if index_word1 is not None and index_word2 is not None:
        inputs1 = tokenizer.encode_plus(phrase1, return_tensors='pt')
        inputs2 = tokenizer.encode_plus(phrase2, return_tensors='pt')

        with torch.no_grad():
            outputs1 = model(**inputs1)
            outputs2 = model(**inputs2)

        embedding1 = outputs1.last_hidden_state[0, index_word1, :]
        embedding2 = outputs2.last_hidden_state[0, index_word2, :]

        similarity = 1 - cosine(embedding1.numpy(), embedding2.numpy())
        print(f"Similarity for '{word}' between '{phrase1}' and '{phrase2}': {similarity:.2f}")
    else:
        print(f"Impossible de calculer la similarité entre '{phrase1}' et '{phrase2}' car le mot '{word}' n'est pas trouvé dans une des deux phrases.")

# Extraction des attentions


c:\Users\Etudiant\M1_TAL\m1-supervised-project\.venv\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Elle fait la lessive tous les samedis pour garder mes vêtements propres.': 0.65
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Julien fait du vélo tous les matins pour rester en forme.': 0.49
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Il fait souvent du cinéma pour attirer la pitié.': 0.71
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'On fait une demande officielle pour obtenir l'autorisation nécessaire.': 0.61
Similarity for 'fait' between 'Il fait marche arrière concernant ma décision.' and 'Coralie fait de la boxe pour améliorer ma condition physique et ma concentration.': 0.35
Similarity for 'fait' between 'Elle fait la lessive tous les samedis pour garder mes vêtements propres.' and 'Julien fait du vélo tous les matins pour rester en forme.': 0.45
Similarity for 'fait' between 'Elle f

In [ ]:
plt.matshow(attention_scores.detach().numpy())
plt.colorbar()
plt.title("Attention Map for 'courir'")
plt.show()           

In [ ]:
# Initialisation du tokenizer et du modèle CamemBERT
model_version = 'camembert-base'
tokenizer = CamembertTokenizer.from_pretrained(model_version)
model = CamembertModel.from_pretrained(model_version, output_attentions=True)

# Liste des phrases avec le verbe 'courir'
phrases = [
    "Il court un péril en allant là-bas.",
    "Le buzz court sur les réseaux sociaux.",
    "Le bruit court dans les couloirs.",
    "Elle court sur la route.",
    "Le danger court dans les zones inexplorées.",
    "Le nuage court dans le ciel orageux.",
    "Le risque court dans chaque décision d'investissement."
]

# Verbe à analyser
word = 'court'

# Analyse des attentions pour chaque phrase
for phrase in phrases:
    tokens = [token.lower() for token in tokenizer.tokenize(phrase)]
    index_word = next((i for i, token in enumerate(tokens) if word in token), None)

    if index_word is not None:
        inputs = tokenizer.encode_plus(phrase, return_tensors='pt')
        with torch.no_grad():
            outputs = model(**inputs)

        # Choisissons les deux premières couches pour l'analyse
        for layer in range(3):  # modif le nombre de couches
            attentions = outputs.attentions[layer]
            attention_scores = attentions[0, :, index_word, :]

            plt.matshow(attention_scores.detach().numpy())
            plt.colorbar()
            plt.title(f"Attention Map for 'courir' in '{phrase}' - Layer {layer+1}")
            plt.xlabel('Token Position')
            plt.ylabel('Attention Head')
            plt.show()
    else:
        print(f"Le mot '{word}' n'a pas été trouvé dans la phrase: '{phrase}'.")


In [29]:
#model.eval()

In [ ]:
"""
# Initialize the model and tokenizer
model_version = 'camembert-base'
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = CamembertTokenizer.from_pretrained(model_version)

# Define the sentences
#sentence_a = "Il porte son attention sur le problème."
#sentence_b = "Il porte un pot de miel à sa grand-mère."
#sentence_a = "Elle éprouve une immense haine pour lui."
#sentence_b = "Elle éprouve de grandes difficultés à finir son projet à temps."
sentence_a = "Il prend une décision importante."
sentence_b = "Il prend un objet dans sa main."
# Tokenize the sentences
inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt', padding=True, truncation=True)

# Extract inputs
input_ids = inputs['input_ids']
attention_mask = inputs['attention_mask']

# Get model outputs, remove token_type_ids since Camembert does not use them
outputs = model(input_ids, attention_mask=attention_mask)
attention = outputs.attentions

# Convert input IDs to tokens for display or further analysis
tokens = tokenizer.convert_ids_to_tokens(input_ids[0])

print("Tokens:", tokens)
"""


BERTVIZ for CamemBERT

In [20]:
model_version = 'camembert-base'
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = CamembertTokenizer.from_pretrained(model_version)

#sentence_a = "Il porte son attention sur le problème."
#sentence_b = "Il porte un pot de miel à sa grand-mère."
#sentence_a = "Elle éprouve une immense haine pour lui."
#sentence_b = "Elle éprouve de grandes difficultés à finir son projet à temps "
sentence_a = "Le bruit court dans les couloirs."
sentence_b = "Elle court sur la route."
inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
input_ids = inputs['input_ids']
attention_mask = inputs['attention_mask']

"""
# Boucle pour traiter chaque phrase
for sentence in phrases:
    inputs = tokenizer(sentence, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    attention_mask = inputs['attention_mask']
"""

# Get model outputs, focusing on attentions
outputs = model(input_ids, attention_mask=attention_mask)
attention = outputs.attentions

# Convert input IDs back to tokens for visualization
tokens = tokenizer.convert_ids_to_tokens(input_ids[0])

head_view(attention, tokens)
model_view(attention, tokens, include_layers=[1,2,3,4])




c:\Users\Etudiant\M1_TAL\m1-supervised-project\.venv\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

BERTviz for bert multilingual

In [51]:
model_version = 'bert-base-multilingual-cased'
model = BertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = BertTokenizer.from_pretrained(model_version)

sentence_a = "Le bruit court dans les couloirs"
sentence_b = "Elle court sur la route"
inputs = tokenizer.encode_plus(sentence_a, sentence_b, return_tensors='pt')
input_ids = inputs['input_ids']
token_type_ids = inputs['token_type_ids']
attention = model(input_ids, token_type_ids=token_type_ids)[-1]
sentence_b_start = token_type_ids[0].tolist().index(1)
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list) 

head_view(attention, tokens, sentence_b_start)
model_view(attention, tokens, sentence_b_start, include_layers=[1,2,3,4])


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [47]:
# Supposons que outputs.last_hidden_state contient les embeddings du dernier état caché
def aggregate_embeddings(input_ids, embeddings):
    # Convertir les ID de tokens en tokens
    tokens = tokenizer.convert_ids_to_tokens(input_ids[0])

    # Dictionnaire pour stocker les embeddings agrégés par mot
    word_embeddings = {}
    current_word = ""
    embeddings_list = []

    for token, embedding in zip(tokens, embeddings[0]):
        if token.startswith("##"):
            # C'est une continuation du mot précédent
            embeddings_list.append(embedding)
        else:
            # C'est un nouveau mot, donc agréger les embeddings précédents si la liste n'est pas vide
            if embeddings_list:
                word_embeddings[current_word] = torch.stack(embeddings_list).mean(dim=0)
                embeddings_list = []
            # Commencer un nouveau mot
            current_word = token
            embeddings_list.append(embedding)

    # N'oubliez pas d'ajouter le dernier mot traité
    if embeddings_list:
        word_embeddings[current_word] = torch.stack(embeddings_list).mean(dim=0)

    return word_embeddings

# Utilisation de la fonction
embeddings = outputs.last_hidden_state  # les embeddings du dernier état caché du modèle
aggregated_embeddings = aggregate_embeddings(input_ids, embeddings)
print(aggregated_embeddings)

{'[CLS]': tensor([-1.1516e-02,  8.9088e-02, -1.8167e-01, -1.9133e-01, -2.4178e-01,
         2.6811e-01, -1.0046e-01,  1.4005e-01, -1.5122e-01,  4.9384e-01,
         2.9650e-01, -6.3293e-02, -2.2387e-01,  4.2568e-01, -7.0899e-01,
         6.5045e-03,  6.0322e-02,  4.0380e-01, -2.3658e-01,  2.3626e-01,
         1.9710e-01,  8.8214e-02, -1.9633e-01,  1.3937e-01, -3.9212e-01,
         4.7036e-02, -2.1208e-01, -1.9907e-01,  6.7495e-01, -2.2829e-01,
         4.8865e-01, -2.3135e-02, -3.4693e-01,  1.2737e-01,  3.3339e-01,
        -9.1627e-02, -1.7550e+00, -2.8518e-01,  3.8693e-02,  1.5355e-01,
         3.0164e-02,  1.9365e-01, -1.9513e-01, -2.4768e-01,  3.2281e-01,
         1.1127e+00,  3.0542e-01, -2.4913e-01,  1.2115e+00, -6.6705e-02,
        -1.4967e-01, -4.6761e-01, -8.2747e-02, -1.3168e+00,  1.6612e-01,
         1.3730e-01, -2.5505e-01,  1.7054e-01,  8.4252e-02, -1.6276e-01,
        -3.2223e-02, -6.2834e-02,  2.2160e-01, -2.6567e-01, -1.4983e-01,
        -8.9761e-02, -1.0030e-01, -1.0947

In [48]:
def aggregate_attention(input_ids, attentions):
    tokens = tokenizer.convert_ids_to_tokens(input_ids[0])
    num_layers = len(attentions)
    num_heads = attentions[0].size(1)
    sequence_length = len(tokens)  # Taille de la séquence après tokenisation
    
    # Initialisation de la matrice d'attention agrégée
    aggregated_attentions = [torch.zeros((num_heads, sequence_length, sequence_length)) for _ in range(num_layers)]
    
    # agrégation spécifique
    for i, layer_attention in enumerate(attentions):
        for head in range(num_heads):
            for token_index, token in enumerate(tokens):
                # Exemple simple : chaque token reçoit l'attention moyenne de ses sous-tokens
                # Assurez-vous de calculer correctement pour chaque token
                aggregated_attentions[i][head, token_index, :] = torch.mean(layer_attention[0, head, token_index, :], dim=0)
                aggregated_attentions[i][head, :, token_index] = torch.mean(layer_attention[0, head, :, token_index], dim=0)
    
    return aggregated_attentions

# Utilisation de la fonction agrégée
aggregated_attentions = aggregate_attention(input_ids, attention)




In [49]:
def aggregate_attention_and_tokens(input_ids, attentions):
    tokens = tokenizer.convert_ids_to_tokens(input_ids[0])
    aggregated_attention = {}
    aggregated_tokens = []
    current_word = ""
    attention_list = []

    for i, token in enumerate(tokens):
        token_attention = attentions[:, :, i, :]  # Prendre toutes les têtes et toutes les couches pour le token i
        if token.startswith("##"):
            attention_list.append(token_attention)
            current_word += token.replace('##', '')
        else:
            if attention_list:
                # Moyenne des attentions sur les indices des sous-mots
                aggregated_attention[current_word] = torch.stack(attention_list).mean(dim=0)
                attention_list = []
            current_word = token.replace('##', '')
            attention_list.append(token_attention)
        if not token.startswith("##"):
            aggregated_tokens.append(current_word)

    # Ajouter le dernier mot
    if attention_list:
        aggregated_attention[current_word] = torch.stack(attention_list).mean(dim=0)

    # Convertir le dictionnaire d'attentions en liste pour compatibilité avec BERTviz
    # Cela suppose que BERTviz accepte une liste d'attentions; sinon, adapter en conséquence.
    attention_list = [aggregated_attention[token] for token in aggregated_tokens if token in aggregated_attention]

    return attention_list, aggregated_tokens

# Utilisation de la fonction
aggregated_attentions, aggregated_tokens = aggregate_attention_and_tokens(input_ids, outputs.attentions[-1])


In [ ]:

# Plotting the embeddings
plt.figure(figsize=(12, 6))
plt.subplot(1, 2, 1)
plt.title('Embedding from Phrase 1')
plt.bar(np.arange(len(embedding1)), embedding1.numpy())
plt.xlabel('Dimension')
plt.ylabel('Value')

plt.subplot(1, 2, 2)
plt.title('Embedding from Phrase 2')
plt.bar(np.arange(len(embedding2)), embedding2.numpy())
plt.xlabel('Dimension')
plt.ylabel('Value')

plt.tight_layout()
plt.show()

In [ ]:
"""
faire: 
"Je fais marche arrière concernant ma décision."
"Je fais la lessive tous les samedis pour garder mes vêtements propres."
"Je fais du vélo tous les matins pour rester en forme."
"Je fais souvent du cinéma pour attirer la pitié."
"Je fais une demande officielle pour obtenir l'autorisation nécessaire."
"Je fais de la boxe pour améliorer ma condition physique et ma concentration."
"""